In [1]:
import itertools
import pandas as pd
import numpy as np
import toytree
import toyplot
import arviz as az
import pymc3 as pm

### Tree and dataframe setup

In [2]:
# generate a random tree
NSPECIES = 80
TREE = toytree.rtree.bdtree(
    ntips=NSPECIES,
    seed=666,
).mod.node_scale_root_height(1.0)

# node idxs that delimit several distinct clades on this tree
CLADES = [152, 153, 154, 155]

# draw and color the four major clades
TREE.draw(
    layout='d', 
    width=500,
    tip_labels=False,
    edge_colors=TREE.get_edge_values_mapped({
        j: toytree.colors[i] for i, j in enumerate(CLADES)
    }),
    scalebar=True,
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t6041cf657bd34496a3f1c994d987bada" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.5 1.0

In [3]:
# make group index (gidx)
crown_dict = {i: TREE.get_tip_labels(i) for i in CLADES}
gidx = np.zeros(TREE.ntips, dtype=int)
for tidx, tip in enumerate(TREE.get_tip_labels()):
    for cidx, clade in enumerate(crown_dict):
        if tip in crown_dict[clade]:
            gidx[tidx] = cidx
gidx

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])

In [73]:
type(gidx[0])

numpy.int64

In [4]:
# True param values
𝛼_mean = 0.05
𝛼_std = 0.02
𝛽_mean = 3.0
𝛽_std = 0.2
𝜓_mean = 0.0
𝜓_std = 0.33

# 4 different clade effects on rate of RI (used for partial-pooling data)
𝜓_0_mean = 1.0
𝜓_0_std = 0.1
𝜓_1_mean = 0.5
𝜓_1_std = 0.05
𝜓_2_mean = -0.5
𝜓_2_std = 0.05
𝜓_3_mean = -1.0
𝜓_3_std = 0.1

In [5]:
# species dataframe
SPECIES_DATA = pd.DataFrame({
    "gidx": gidx,
    "b": np.random.normal(𝛽_mean, 𝛽_std, TREE.ntips),
    "psi": np.random.normal(𝜓_mean, 𝜓_std, TREE.ntips),
    "psi_x": np.concatenate([
        np.random.normal(𝜓_0_mean, 𝜓_0_std, len(gidx[gidx == 0])),
        np.random.normal(𝜓_1_mean, 𝜓_1_std, len(gidx[gidx == 1])),
        np.random.normal(𝜓_2_mean, 𝜓_2_std, len(gidx[gidx == 2])),
        np.random.normal(𝜓_3_mean, 𝜓_3_std, len(gidx[gidx == 3])),
    ]),
})
SPECIES_DATA.head()

gidx         b       psi     psi_x
0     0  2.570468 -0.236524  0.997529
1     0  3.292698 -0.624017  0.863576
2     0  2.936227 -0.612795  0.956139
3     0  2.746916 -0.234236  1.115301
4     0  2.767121  0.031270  0.981499

### Generate crossing data

In [6]:
def get_dist(tree, idx0, idx1):
    "returns the genetic distance between two nodes on a tree"
    dist = tree.treenode.get_distance(
        tree.idx_dict[idx0], 
        tree.idx_dict[idx1],
    )
    return dist

# get all combinations of two sampled taxa
a, b = zip(*itertools.combinations(range(NSPECIES), 2))

# organize into DF and get genetic distance between pairs
DATA = pd.DataFrame({
    "sidx0": a,
    "sidx1": b,
    "dist": [(get_dist(TREE, i, j) / 2) for (i, j) in zip(a, b)],
})

DATA['b'] = np.random.normal(𝛽_mean, 𝛽_std, DATA.shape[0])
DATA['velo'] = (
    DATA['b']
    + SPECIES_DATA['psi'][DATA.sidx0].values
    + SPECIES_DATA['psi'][DATA.sidx1].values
)
DATA['velo_x'] = (
    DATA['b']
    + SPECIES_DATA['psi_x'][DATA.sidx0].values
    + SPECIES_DATA['psi_x'][DATA.sidx1].values
)
DATA['intercept'] = np.random.normal(𝛼_mean, 𝛼_std, DATA.shape[0])
# DATA['error'] = np.random.normal(0.0, 𝜎_std, DATA.shape[0])

# get logits
DATA['logit_b'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.b * np.log(DATA.dist))))
)
DATA['logit'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.velo * np.log(DATA.dist))))
)
DATA['logit_x'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.velo_x * np.log(DATA.dist))))
)

# get RI estimates
DATA['RI_pooled'] = np.random.binomial(n=1, p=DATA.logit_b / DATA.logit_b.max())
DATA['RI_unpooled'] = np.random.binomial(n=1, p=DATA.logit / DATA.logit.max())
DATA['RI_partpooled'] = np.random.binomial(n=1, p=DATA.logit_x / DATA.logit_x.max())

DATA.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0      0      1  0.073376  2.881579  2.021039  4.742684   0.023752  0.000551   
1      0      2  0.089748  2.638508  1.789189  4.592176   0.074466  0.001858   
2      0      3  0.129770  3.113867  2.643107  5.226697   0.055129  0.001827   
3      0      4  0.144542  3.059197  2.853944  5.038226   0.059521  0.002850   
4      0      5  0.144542  2.620887  2.866354  4.699434   0.059066  0.006625   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.005192  0.000004          0            0              0  
1  0.014219  0.000017          0            0              0  
2  0.004763  0.000024          0            0              0  
3  0.004233  0.000062          0            0              0  
4  0.004131  0.000120          0            0              0

In [7]:
NSAMPLES = 2000
SAMPLE = DATA.sample(NSAMPLES).copy().reset_index(drop=True)
SAMPLE.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0     60     63  0.578689  2.921440  2.625589  1.913308   0.044766  0.174620   
1     46     74  0.592720  3.287330  3.246154  1.886728   0.043472  0.157638   
2     23     30  0.438896  2.615066  2.010742  4.803178   0.057368  0.109475   
3     61     71  0.592720  3.160457  2.911351  1.778620   0.020785  0.163524   
4     23     34  0.590047  3.069562  2.832857  4.990309   0.039344  0.170794   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.199184  0.268589          0            0              1  
1  0.160519  0.280225          1            1              0  
2  0.168197  0.019879          0            1              0  
3  0.182136  0.287104          1            0              1  
4  0.189212  0.069570          0            0              0

### Visualize data

In [8]:
def logit_plot(dist, logit, RI):
    canvas = toyplot.Canvas(width=500, height=250)
    ax0 = canvas.cartesian(
        label="pooled data (function)",
        xlabel="Genetic dist.",
        ylabel="Logit function",
        grid=(1, 2, 0),
    )
    ax1 = canvas.cartesian(
        label="pooled data (observation)",
        xlabel="Genetic dist.",
        ylabel="RI",
        grid=(1, 2, 1),
    )

    # points are jittered on x-axis for visibility
    ax0.scatterplot(
        dist,
        logit,
        size=5,
        opacity=0.33,
        color=toyplot.color.Palette()[0],
    );
    ax1.scatterplot(
        dist,
        RI,
        size=10,
        opacity=0.2,
        marker="|",
        mstyle={
            "stroke": toyplot.color.Palette()[1],
            "stroke-width": 3,
        },
    );
    return canvas, (ax0, ax1)

In [9]:
logit_plot(SAMPLE.dist, SAMPLE.logit_b, SAMPLE.RI_pooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t317f0be3f508470cb9a6856b3ef5c811" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0" transform="translate(199.9

In [10]:
logit_plot(SAMPLE.dist, SAMPLE.logit, SAMPLE.RI_unpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="ta634672b80914af6bdbfab35334e5f22" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0" transform="translate(19

In [11]:
logit_plot(SAMPLE.dist, SAMPLE.logit_x, SAMPLE.RI_partpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t544b2d0afb3b422587273e716ebd1aa4" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0" transform="translate(199.999

### Define models

In [12]:
def pooled_logistic(x, y, **kwargs):
    
    # define model
    with pm.Model() as model:  

        # parameters and error
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 𝛼 + 𝛽 * np.log(x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [13]:
def unpooled_logistic(x, y, idx0, idx1, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0.values)
        sidx1 = pm.Data("spp_idx1", idx1.values)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=1)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=1)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean + 𝜓_std * 𝜓_offset)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * np.log(x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(init = 'adapt_diag', **kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [14]:
def partpooled_logistic(x, y, idx0, idx1, gidx, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0)
        sidx1 = pm.Data("spp_idx1", idx1)
        gidx = pm.Data("gidx", gidx)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=4)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=4)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean[gidx] + 𝜓_std[gidx] * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        
        # linear model prediction
        effect = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * np.log(x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood (normal distributed errors)
        y = pm.Bernoulli("y", p=logit, observed=y)

        # sample posterior, skip burnin
        trace = pm.sample(init = 'adapt_diag', **kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

### Functions to plot results

In [15]:
def toytrace(trace, var_names, titles):
    """
    Plot posterior trace with toyplot
    """
    nvars = len(var_names)
    
    # setup canvase
    canvas = toyplot.Canvas(width=500, height=200 * nvars)
    
    # store axes
    axes = []
    
    # iter over params
    for pidx, param in enumerate(var_names):
        
        # get param posterior
        posterior = trace.get_values(param)
        
        # setup axes 
        ax = canvas.cartesian(grid=(nvars, 1, pidx))
        ax.y.show = False
        ax.x.spine.style = {"stroke-width": 1.5}
        ax.x.ticks.labels.style = {"font-size": "12px"}
        ax.x.ticks.show = True
        ax.x.label.text = f"param='{titles[pidx]}'"        
        
        # iterate over shape of param
        for idx in range(posterior.shape[1]):
            mags, bins = np.histogram(posterior[:, idx], bins=100)
            ax.plot(bins[1:], mags, stroke_width=2, opacity=0.6)
        axes.append(ax)
    return canvas, axes

In [16]:
import scipy.stats as stats

def draw_velocity_dists(trace, baseline=0.15):
    """
    Draw the clade velocities as gaussians
    """
    canvas = toyplot.Canvas(width=350, height=300)
    axes = canvas.cartesian(xlabel="Relative velocity of reproductive isolation")
    marks = []
    base = 0
    for i in range(trace['𝜓_mean'].shape[1]):
        
        loc = trace['𝜓_mean'][:, i].mean()
        scale = trace['𝜓_std'][:, i].mean()
        interval = stats.norm.interval(0.995, loc, scale)
        points = np.linspace(interval[0], interval[1], 100)
        mark = axes.fill(
            points, 
            stats.norm.pdf(points, loc=loc, scale=scale), 
            style={
                "fill-opacity": 0.45,
                "stroke": 'black',
                "stroke-opacity": 1.0,
                "stroke-width": 1,
            },
            baseline=np.repeat(base, 100),
        )
        marks.append(mark)
        axes.hlines(base, style={"stroke-dasharray": "5,5", 'stroke-width': 1})
        base += baseline
        
    axes.y.show = False
    axes.x.ticks.locator = toyplot.locator.Extended(only_inside=True)
    axes.x.ticks.show = True
    return canvas, axes, marks

In [17]:
# MCMC sampler kwargs
sample_kwargs = dict(
    tune=10000,
    draws=10000,
    target_accept=0.99,
    return_inferencedata=False,
    progressbar=True,
)

### Run three datasets under pooled model

In [18]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_pooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
INFO (theano.gof.compilelock): Waiting for existing lock by process '23859' (I am process '23901')
INFO (theano.gof.compilelock): To manually release the lock, delete /home/henry/.theano/compiledir_Linux-4.15--generic-x86_64-with-debian-buster-sid-x86_64-3.7.9-64/lock_dir
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 306 seconds.


In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_unpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


In [33]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_partpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 290 seconds.


### Run three datasets under unpooled model

In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_pooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


In [37]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_unpooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 15749 seconds.


In [39]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_partpooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 13111 seconds.


### Run three datasets under partpooled model

In [41]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_pooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 9263 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [42]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_unpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 10714 seconds.


In [19]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_partpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 7628 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [20]:
partpooled_model_partpooled_data['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  \
𝜓_mean[0]    1.142  2.262  -3.151    5.325      0.029    0.020    6153.0   
𝜓_mean[1]    3.587  2.301  -0.785    7.850      0.029    0.021    6268.0   
𝜓_mean[2]   -0.428  2.252  -4.565    3.870      0.029    0.020    6141.0   
𝜓_mean[3]   -1.377  2.251  -5.638    2.835      0.029    0.020    6121.0   
𝜓_offset[0]  0.004  0.889  -1.641    1.707      0.004    0.005   43499.0   
...            ...    ...     ...      ...        ...      ...       ...   
logit[1995]  0.072  0.066   0.003    0.191      0.000    0.000   27030.0   
logit[1996]  0.000  0.001   0.000    0.001      0.000    0.000   29645.0   
logit[1997]  0.724  0.062   0.607    0.839      0.000    0.000   24250.0   
logit[1998]  0.721  0.057   0.615    0.834      0.000    0.000   42599.0   
logit[1999]  0.950  0.007   0.937    0.962      0.000    0.000   44058.0   

              ess_sd  ess_bulk  ess_tail  r_hat  
𝜓_mean[0]     6153.0    6154.0   11052.0    1.0  
𝜓_mean[1]     6268.0    6269.0   11533.0    1.0  
𝜓_mean[2]     6141.0    6143.0   10759.0    1.0  
𝜓_mean[3]     6121.0    6121.0   10875.0    1.0  
𝜓_offset[0]  16471.0   43550.0   26129.0    1.0  
...              ...       ...       ...    ...  
logit[1995]  27030.0   30047.0   29931.0    1.0  
logit[1996]  29645.0   24079.0   28904.0    1.0  
logit[1997]  24102.0   24009.0   29657.0    1.0  
logit[1998]  42599.0   42730.0   30753.0    1.0  
logit[1999]  43985.0   43005.0   25701.0    1.0  

[2170 rows x 11 columns]

In [28]:
toytrace(partpooled_model_partpooled_data['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="t60048fba6b3540eb924b377c84792a30" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 101.56218416634766 149.92193598750976 L 104.6886159023415 150.0 L 107.8150476383353 149.92193598750976 L 110.94147937432913 150.0 L 114.06791111032297 149.92193598750976 L 117.19434284631679 149.68774395003905 L 120.32077458231062 149.6096799375488 L 123.44720631830445 149.76580796252927 L 126.57363805429827 148.82903981264636 L 129.7000697902921 149.29742388758783 L 132.82650152628594 149.37548790007807 L 135.95293326227977 148.59484777517565 L 139.0793649982736 148.9071038251366 L 142.20579673426744 147.81420765027323 L 145.33222847026127 147.97033567525372 L 148.45866020625508 147.423887587822 L 151.5850919422489 146.6432474629196 L 154.7115236782427 145.5503512880562 L 157.83795541423657 144.3793911007026 L 160.96438715023038 141.88134270101483 L 164.09081888622424 142.27166276346605 L 167.21725062221807 140.78844652615143 L 170.34368235821188 139.2271662763466 L 173.4701140942057 138.6807181889149 L 176.59654583019955 133.13817330210773 L 179.72297756619338 132.27946916471507 L 182.84940930218718 129.78142076502732 L 185.97584103818102 126.50273224043715 L 189.10227277417485 123.92661982825916 L 192.22870451016868 119.71116315378612 L 195.35513624616252 113.544106167057 L 198.48156798215632 111.28024980483997 L 201.60799971815015 106.67447306791568 L 204.73443145414402 97.69711163153785 L 207.86086319013782 95.35519125683061 L 210.98729492613165 90.98360655737704 L 214.1137266621255 80.91334894613584 L 217.24015839811932 77.79078844652615 L 220.3665901341131 72.40437158469945 L 223.49302187010696 71.31147540983608 L 226.6194536061008 67.87665886026541 L 229.74588534209462 65.84699453551912 L 232.87231707808846 58.35284933645589 L 235.9987488140823 60.92896174863388 L 239.1251805500761 58.040593286494925 L 242.25161228606996 60.61670569867291 L 245.37804402206376 54.68384074941452 L 248.5044757580576 53.43481654957065 L 251.63090749405146 56.24512099921936 L 254.75733923004523 64.6760343481655 L 257.88377096603904 58.89929742388759 L 261.0102027020329 60.85089773614364 L 264.1366344380267 66.70569867291178 L 267.26306617402054 69.35987509758002 L 270.38949791001437 75.52693208430912 L 273.5159296460082 75.99531615925059 L 276.64236138200204 82.24043715846994 L 279.76879311799587 89.4223263075722 L 282.8952248539897 90.1249024199844 L 286.02165658998354 97.15066354410615 L 289.1480883259773 97.22872755659641 L 292.2745200619712 103.31772053083527 L 295.40095179796504 107.92349726775956 L 298.5273835339588 112.21701795472288 L 301.6538152699527 114.87119437939111 L 304.78024700594653 124.39500390320062 L 307.90667874194037 127.98594847775176 L 311.03311047793414 128.14207650273224 L 314.15954221392803 132.43559718969556 L 317.2859739499218 135.16783762685404 L 320.4124056859157 136.02654176424667 L 323.5388374219094 139.38329430132708 L 326.66526915790325 141.4129586260734 L 329.79170089389714 143.5206869633099 L 332.91813262989103 144.14519906323184 L 336.0445643658848 145.9406713505074 L 339.17099610187864 146.4871194379391 L 342.2974278378725 146.6432474629196 L 345.4238595738663 146.6432474629196 L 348.5502913098601 147.65807962529274 L 351.6767230458539 147.58001561280247 L 354.80315478184775 148.9071038251366 L 357.92958651784164 148.43871975019516 L 361.0560182538354 148.7509758001561 L 364.1824499898292 149.45355191256832 L 367.3088817258231 149.68774395003905 L 370.4353134618169 149.68774395003905 L 373.56174519781075 149.76580796252927 L 376.6881769338045 149.76580796

In [29]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi_x'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    color=[toyplot.color.Palette()[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tedc08b208fbc45038fc4a3e5a0a1ef47" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -2 0 2 4 ESTIMATED species velocity -1 0 1 TRUE species velocity

In [52]:
stats.linregress(partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

LinregressResult(slope=0.4097000024421494, intercept=-0.024422366652693817, rvalue=0.7284554262119658, pvalue=1.8875221785048892e-14, stderr=0.04362800347892822)

In [64]:
from scipy.stats import f_oneway
from statsmodels.stats.multicomp import pairwise_tukeyhsd

In [57]:
clade1 = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0)[:36]
clade2 = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0)[36:45]
clade3 = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0)[45:66]
clade4 = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0)[66:]

In [65]:
f_oneway(clade1, clade2, clade3, clade4)

F_onewayResult(statistic=427.0931278038688, pvalue=1.8361050881981055e-47)

In [69]:
tukey = pairwise_tukeyhsd(endog = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0),
                          groups = gidx,
                          alpha = 0.05)
print(tukey)

Multiple Comparison of Means - Tukey HSD, FWER=0.05
group1 group2 meandiff p-adj  lower   upper  reject
---------------------------------------------------
     0      1   2.4561 0.001  2.1011  2.8111   True
     0      2  -1.5731 0.001 -1.8346 -1.3115   True
     0      3  -2.5206 0.001 -2.8207 -2.2206   True
     1      2  -4.0291 0.001 -4.4087 -3.6496   True
     1      3  -4.9767 0.001 -5.3837 -4.5697   True
     2      3  -0.9476 0.001 -1.2763 -0.6189   True
---------------------------------------------------


In [30]:
draw_velocity_dists(partpooled_model_partpooled_data['trace'], baseline = 1.2);

<svg class="toyplot-canvas-Canvas" height="300.0px" id="t05d34ce59e574ab08e75cbe16016e817" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <polygon points="78.94983299237329,250.0 80.5767464329428,250.0 82.20365987351232,250.0 83.83057331408183,250.0 85.45748675465134,250.0 87.08440019522087,250.0 88.71131363579036,250.0 90.33822707635989,250.0 91.96514051692938,250.0 93.59205395749892,250.0 95.21896739806843,250.0 96.84588083863795,250.0 98.47279427920745,250.0 100.09970771977697,250.0 101.72662116034647,250.0 103.35353460091599,250.0 104.9804480414855,250.0 106.60736148205503,250.0 108.23427492262452,250.0 109.86118836319403,250.0 111.48810180376356,250.0 113.11501524433307,250.0 114.74192868490258,250.0 116.3688421254721,250.0 117.99575556604161,250.0 119.62266900661112,250.0 121.24958244718064,250.0 122.87649588775014,250.0 124.50340932831966,250.0 126.13032276888916,250.0 127.7572362094587,250.0 129.38414965002818,250.0 131.0110630905977,250.0 132.63797653116723,250.0 134.26488997173672,250.0 135.89180341230627,250.0 137.51871685287574,250.0 139.1456302934453,250.0 140.7725437340148,250.0 142.3994571745843,250.0 144.0263706151538,250.0 145.6532840557233,250.0 147.28019749629286,250.0 148.90711093686235,250.0 150.53402437743188,250.0 152.16093781800137,250.0 153.7878512585709,250.0 155.4147646991404,250.0 157.04167813970992,250.0 158.66859158027944,250.0 160.29550502084896,250.0 161.9224184614185,250.0 163.54933190198798,250.0 165.17624534255748,250.0 166.803158783127,250.0 168.43007222369653,250.0 170.05698566426605,250.0 171.68389910483555,250.0 173.31081254540507,250.0 174.93772598597457,250.0 176.5646394265441,250.0 178.1915528671136,250.0 179.8184663076831,250.0 181.4453797482526,250.0 183.0722931888221,250.0 184.69920662939165,250.0 186.32612006996118,250.0 187.95303351053067,250.0 189.5799469511002,250.0 191.2068603916697,250.0 192.83377383223922,250.0 194.46068727280874,250.0 196.0876007133782,250.0 197.71451415394773,250.0 199.34142759451726,250.0 200.96834103508678,250.0 202.5952544756563,250.0 204.22216791622583,250.0 205.8490813567953,250.0 207.47599479736482,250.0 209.10290823793437,250.0 210.7298216785039,250.0 212.35673511907333,250.0 213.98364855964286,250.0 215.6105620002124,250.0 217.2374754407819,250.0 218.86438888135143,250.0 220.4913023219209,250.0 222.11821576249045,250.0 223.74512920305995,250.0 225.37204264362947,250.0 226.99895608419902,250.0 228.62586952476846,250.0 230.252782965338,250.0 231.87969640590754,250.0 233.5066098464771,250.0 235.1335232870466,250.0 236.76043672761605,250.0 238.38735016818558,250.0 240.01426360875507,250.0 240.01426360875507,249.64259291772444 238.38735016818558,249.58159573289717 236.76043672761605,249.51176100258482 235.1335232870466,249.43209952177526 233.5066098464771,249.34156120291075 231.87969640590754,249.23903969895127 230.252782965338,249.12337874378036 228.62586952476846,248.99338035189618 226.99895608419902,248.84781499676836 225.37204264362947,248.68543385788365 223.74512920305995,248.50498319021747 222.11821576249045,248.3052208267402 220.4913023219209,248.08493477492254 218.86438888135143,247.84296381265108 217.2374754407819,247.5782199283841 215.6105620002124,247.28971238595867 213.98364855964286,246.97657312766233 212.35673511907333,246.638083161755 210.7298216785039,246.27369951454662 209.10290823793437,245.883082264581 207.47599479736482,245.46612111976444 205.8490813567953,245.02296094979795 204.22216791622583,244.55402564839642 202.5952544756563,244.06003967478517 200.96834103508678,243.5420466139323 199.34142759451726,243.00142410169457 197.7145141

In [24]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_partpooled_data_2 = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 7189 seconds.
The number of effective samples is smaller than 25% for some parameters.


### Assess model fit

In [43]:
def rmse(predictions, targets):
    differences = predictions - targets                       #the DIFFERENCEs.
    differences_squared = differences ** 2                    #the SQUAREs of ^
    mean_of_differences_squared = differences_squared.mean()  #the MEAN of ^
    rmse_val = np.sqrt(mean_of_differences_squared)           #ROOT of ^
    return rmse_val   

In [44]:
def aicm(mean, variance):
    return 2*mean - 2*variance

In [45]:
rmse(unpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi'])

1.6829399085369496

In [46]:
rmse(partpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

1.2960935050421183

In [47]:
aicm(unpooled_sub['trace']['𝜓'].mean(), unpooled_sub['trace']['𝜓'].var())

-24.07642765287162

In [48]:
# Raftery et al. (2007) holds that this value is better.  R+M disagree?
aicm(partpooled_sub['trace']['𝜓'].mean(), partpooled_sub['trace']['𝜓'].var())

-17.436591387294683

In [43]:
az_pooled_model_pooled_data = az.from_pymc3(trace = pooled_model_pooled_data['trace'], 
                                            model = pooled_model_pooled_data['model'])
az_pooled_model_unpooled_data = az.from_pymc3(trace = pooled_model_unpooled_data['trace'], 
                                            model = pooled_model_unpooled_data['model'])
az_pooled_model_partpooled_data = az.from_pymc3(trace = pooled_model_partpooled_data['trace'], 
                                            model = pooled_model_partpooled_data['model'])
az_unpooled_model_pooled_data = az.from_pymc3(trace = unpooled_model_pooled_data['trace'], 
                                            model = unpooled_model_pooled_data['model'])
az_unpooled_model_unpooled_data = az.from_pymc3(trace = unpooled_model_unpooled_data['trace'], 
                                            model = unpooled_model_unpooled_data['model'])
az_unpooled_model_partpooled_data = az.from_pymc3(trace = unpooled_model_partpooled_data['trace'], 
                                            model = unpooled_model_partpooled_data['model'])
az_partpooled_model_pooled_data = az.from_pymc3(trace = partpooled_model_pooled_data['trace'], 
                                            model = partpooled_model_pooled_data['model'])
az_partpooled_model_unpooled_data = az.from_pymc3(trace = partpooled_model_unpooled_data['trace'], 
                                            model = partpooled_model_unpooled_data['model'])
az_partpooled_model_partpooled_data = az.from_pymc3(trace = partpooled_model_partpooled_data['trace'], 
                                            model = partpooled_model_partpooled_data['model'])

### Compare models with different datasets

In [44]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "pooled_model_unpooled_data": az_pooled_model_unpooled_data, 
            "pooled_model_partpooled_data": az_pooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo     weight  \
pooled_model_pooled_data        0 -671.566  2.36585        0   0.939415   
pooled_model_unpooled_data      1 -731.398  2.43399  59.8321  0.0505505   
pooled_model_partpooled_data    2 -748.108  2.27983  76.5417  0.0100344   

                                   se      dse warning loo_scale  
pooled_model_pooled_data       28.227        0   False       log  
pooled_model_unpooled_data    27.5029  36.3381   False       log  
pooled_model_partpooled_data  28.3927  36.4838   False       log

In [45]:
az.compare({"unpooled_model_pooled_data": az_unpooled_model_pooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo    d_loo     weight  \
unpooled_model_partpooled_data    0 -653.247    67.42        0   0.665399   
unpooled_model_pooled_data        1  -669.19  43.1989  15.9432   0.315437   
unpooled_model_unpooled_data      2 -711.826  61.2518  58.5794  0.0191642   

                                     se      dse warning loo_scale  
unpooled_model_partpooled_data   27.771        0    True       log  
unpooled_model_pooled_data      27.6958  36.4485    True       log  
unpooled_model_unpooled_data    27.6136  35.7013    True       log

In [46]:
az.compare({"partpooled_model_pooled_data": az_partpooled_model_pooled_data,
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo    d_loo     weight  \
partpooled_model_partpooled_data    0 -633.661  34.4304        0   0.761856   
partpooled_model_pooled_data        1  -661.35  36.1488  27.6888   0.221655   
partpooled_model_unpooled_data      2  -707.56  59.6532  73.8992  0.0164888   

                                       se      dse warning loo_scale  
partpooled_model_partpooled_data  28.9238        0    True       log  
partpooled_model_pooled_data      27.6402  36.7298    True       log  
partpooled_model_unpooled_data    27.8861  36.3287    True       log

### Compare datasets with different models

In [53]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "unpooled_model_pooled_data": az_unpooled_model_pooled_data, 
            "partpooled_model_pooled_data": az_partpooled_model_pooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo    d_loo     weight  \
partpooled_model_pooled_data    0  -661.35  36.1488        0   0.868866   
unpooled_model_pooled_data      1  -669.19  43.1989  7.84063  0.0426719   
pooled_model_pooled_data        2 -671.566  2.36585  10.2167  0.0884621   

                                   se      dse warning loo_scale  
partpooled_model_pooled_data  27.7726        0    True       log  
unpooled_model_pooled_data    27.6873  5.46395    True       log  
pooled_model_pooled_data      27.6038  7.76121   False       log

In [54]:
az.compare({"pooled_model_unpooled_data": az_pooled_model_unpooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo    d_loo      weight  \
partpooled_model_unpooled_data    0  -707.56  59.6532        0    0.788881   
unpooled_model_unpooled_data      1 -711.826  61.2518  4.26646    0.203478   
pooled_model_unpooled_data        2 -731.398  2.43399  23.8385  0.00764122   

                                     se      dse warning loo_scale  
partpooled_model_unpooled_data  27.3327        0    True       log  
unpooled_model_unpooled_data    27.1613  5.45838    True       log  
pooled_model_unpooled_data      27.5589  10.7491   False       log

In [55]:
az.compare({"pooled_model_partpooled_data": az_pooled_model_partpooled_data,
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo    d_loo       weight  \
partpooled_model_partpooled_data    0 -633.661  34.4304        0     0.999325   
unpooled_model_partpooled_data      1 -653.247    67.42  19.5862   0.00067481   
pooled_model_partpooled_data        2 -748.108  2.27983  114.447  1.92963e-27   

                                       se      dse warning loo_scale  
partpooled_model_partpooled_data  27.6553        0    True       log  
unpooled_model_partpooled_data    26.8215  5.96982    True       log  
pooled_model_partpooled_data      27.0832  17.2672   False       log

### other stuff

In [48]:
# Save trace.  To load in different notebook, model context and sample data is required.
pm.save_trace(partpooled_model_partpooled_data['trace'], directory = "/home/henry/oaks-thesis/trace/logarithmic-pmpd")

'/home/henry/oaks-thesis/trace/logarithmic-pmpd'

In [49]:
logarithmic_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

In [50]:
# Magic command to move sample data across notebooks.   
%store logarithmic_args

Stored 'logarithmic_args' (list)
